In [1]:
#|default_exp triangle_condition_curvature
# Standard libraries
import os
import math
import numpy as np
import time
from fastcore.all import *
from nbdev.showdoc import *
from tqdm.auto import tqdm, trange
# Configure environment


## Imports for plotting
import matplotlib.pyplot as plt
%matplotlib inline
from IPython.display import set_matplotlib_formats
# set_matplotlib_formats('svg', 'pdf') # For export
from matplotlib.colors import to_rgba
import seaborn as sns
sns.set()

## Progress bar
from tqdm.auto import tqdm

## project specifics
import autometric
import torch

from autometric.utils import *

%load_ext autoreload
%autoreload 2

# Triangle Condition Curvature
> Evaluating geodesics using Alexandrov geometry

In [315]:
show_doc(compute_triangle_curvatures)

---

### compute_triangle_curvatures

>      compute_triangle_curvatures (X:numpy.ndarray, D:numpy.ndarray,
>                                   geodesic_fn, num_triangles=100,
>                                   min_edge_length=1, max_edge_length=1.5)

Compures the Alexandrov curvature of sampled triangles. Returns ks, middle_idxs; ks is a list of Alexandrov curvatures, and middle_idxs is a list of the indices of the middle point of each triangle.

|    | **Type** | **Default** | **Details** |
| -- | -------- | ----------- | ----------- |
| X | ndarray |  | pointcloud |
| D | ndarray |  | distances on pointcloud; preferable manifold distances (PHATE). Used for creating triangles. Doesn't need to come from the geodesics. |
| geodesic_fn |  |  | function that takes start_points, end_points and ts and returns (a list of geodesics, length of each geodesic) |
| num_triangles | int | 100 |  |
| min_edge_length | int | 1 | Must tune to each dataset. Defaults for torus. |
| max_edge_length | float | 1.5 |  |

# Implementation

We create a test point cloud (the torus), and 
1. Convert it into an o3d format, compute nearest neighbor distances.
2. Downsample to the appropriate size
3. Create a mesh with the appropriate number of triangles

In [2]:
from autometric.datasets import Torus, SwissRoll

INFO: Using pytorch backend


In [283]:
from sklearn.metrics.pairwise import pairwise_distances
torus = Torus(num_points = 3000)
X_torus = torus.X.numpy()
D_euc = pairwise_distances(X_torus, X_torus)
swiss_roll = SwissRoll(num_points = 10000)
D_swiss_roll = pairwise_distances(swiss_roll.X, swiss_roll.X)

In [284]:
#|export
import numpy as np
# def create_triangles_from_pointcloud(
#     X:np.ndarray, 
#     D:np.ndarray, # manifold distance matrix of X; shape (num_points, num_points).
#     min_dist:float=0.1, # triangle edges must length greater than this
#     num_triangles=100,
#     ):
#     """
#     Create a set of triangles from a pointcloud. This is not a mesh; just a set of triangles with edge lengths around min_dist.
#     Returns np.ndarray of shape (num_triangles, 3). Each row is a triangle; each entry is an index in X.
#     """
#     # subsample num_triangles points from X
#     idxs = np.random.choice(X.shape[0], num_triangles, replace=False)
#     # for each idx, construct one triangle by matching two points - both of which have distances greater than min_dist
#     sub_D = D[idxs]
#     triangles = []
#     for i in range(num_triangles):
#         # find two points with distances greater than min_dist
#         idxs = np.where(sub_D[i,:] > min_dist)[0]
#         if len(idxs) == 0:
#             continue
#         # find the two points with the smallest distance
#         idxs = idxs[np.argsort(sub_D[i,idxs])]
#         # add the two points to the triangle
#         triangles.append([idxs[0], idxs[1], idxs[2]])
#     return np.array(triangles)

def create_triangles_from_pointcloud(
    X:np.ndarray, 
    D:np.ndarray, # manifold distance matrix of X; shape (num_points, num_points).
    min_dist:float=0.1, # triangle edges must length greater than this
    max_dist:float=0.3,
    num_triangles=100,
    hypotenuse_less_than = 1.7, # the hypotenuse times this should be less than the sum of the other two sides
    ):
    triangles = []
    while len(triangles) < num_triangles:
        candidate_idxs = np.random.choice(X.shape[0], num_triangles, replace=False)
        for a in candidate_idxs:
            # find idxs of points with distances greater than min_dist from a
            idxs = np.where((D[a,:] > min_dist) & (D[a,:] < max_dist))[0]
            if len(idxs) == 0:
                continue
            # sort by distance from a
            idxs = idxs[np.argsort(D[a,idxs])]
            for b in idxs:
                # find idxs of points with distances greater than min_dist from b and a
                idxs = np.where((D[b,:] > min_dist) & (D[b,:] < max_dist) & (D[a,:] > min_dist) & (D[a,:] < max_dist) & ((D[a, :] + D[b,:]) > hypotenuse_less_than*D[a,b]))[0]
                if len(idxs) == 0:
                    continue
                else:
                    # sort by distance from a and b
                    idxs = idxs[np.argsort(D[b,idxs] + D[a,idxs])]
                    if isinstance(idxs, int): idxs = [idxs]
                    for c in idxs:
                        if (D[a, b] + D[b,c]) > hypotenuse_less_than*D[a,c] and (D[a, c] + D[a, b]) > hypotenuse_less_than*D[b,c]:
                            triangles.append([a, b, c])
                            break
                    break
    return np.array(triangles)[:num_triangles]

In [285]:
triangles = create_triangles_from_pointcloud(X_torus, D_euc, min_dist = 1, max_dist=1.5, num_triangles=14)

In [250]:
swiss_roll_triangles = create_triangles_from_pointcloud(swiss_roll.X, D_swiss_roll, min_dist = 10, max_dist = 12, num_triangles = 100, hypotenuse_less_than=1.9)

In [222]:
plot_triangle_in_3d(swiss_roll.X, swiss_roll_triangles[10], swiss_roll.geodesics)

/tmp/ipykernel_210617/792130572.py:5: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

/tmp/ipykernel_210617/792130572.py:6: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [197]:
#|export
def get_geodesics_from_triangle(geodesic_fn, X, triangle_idxs, t = np.linspace(0,1,100)):
    start_idxs = [triangle_idxs[0], triangle_idxs[0], triangle_idxs[1]]
    end_idxs = [triangle_idxs[1], triangle_idxs[2], triangle_idxs[2]]
    start_points = torch.tensor(X[start_idxs])
    end_points = torch.tensor(X[end_idxs])
    points, lengths = geodesic_fn(start_points, end_points, t)
    return points, lengths

In [198]:
#|export
from autometric.utils import plot_3d_with_geodesics
def plot_triangle_in_3d(X, triangle_idxs, geodesic_fn):
    gs, lengths = get_geodesics_from_triangle(geodesic_fn, X, triangle_idxs)
    plot_3d_with_geodesics(X, gs, title=f"Triangle {triangle_idxs}")
    

In [201]:
plot_triangle_in_3d(X_torus, triangles[2], geodesic_fn=torus.geodesics)

It's notable that even on this 3000 point noiseless torus, using Dijkstra for shortest paths, it's not doing very well. The triangles generated with Dijkstra Geodesics are very noisy. Occasional bits of sparsity are trending it away from the true line, creating fat triangles where they should be skinny, and vice versa.

This raises the possibility that our method can possibly outperform Dijkstra, even in noiseless, fairly densely sampled data.

In [291]:
#|export
def euclidean_section_length(
    a, # length from b' to c'
    b, # length from c' to a'
    c, # length from a' to b'
    c1 # length from b' to midpoint
    ):
    # computes the euclidean length of an edge running from vertex c' to a midpoint c1 on edge opposite
    inner = c1**2 + a**2 + c1*((b**2 - a**2 - c**2)/c)
    return inner**0.5
    # computes the euclidean length of an edge running from vertex c' to a midpoint on the edge opposite, c1

def alexandrov_curvature_of_triangle(X, triangle_idxs, geodesic_fn, return_extras = False):
    gs, lengths = get_geodesics_from_triangle(
        geodesic_fn, X, triangle_idxs
    )
    # three lengths are a, b, c. 
    a = lengths[0]
    b = lengths[1]
    c = lengths[2]
    # choose midpoint in third geodesic
    midpoint = gs[2][len(gs[2])//2]
    (c1_geodesic, d_geodesic), (c1, d) = geodesic_fn(X[[triangle_idxs[1], triangle_idxs[0]]], np.vstack([midpoint, midpoint]), np.linspace(0,1,100))
    d_euclidean = euclidean_section_length(a, b, c, c1)
    k = d - d_euclidean
    if return_extras:
        return k, gs, c1_geodesic, d_geodesic
    else:
        return k

In [292]:
k, gs, c1_geodesic, d_geodesic = alexandrov_curvature_of_triangle(X_torus, triangles[0], torus.geodesics, return_extras = True)

In [293]:
k

tensor(0.2752, dtype=torch.float64)

A sanity check that we are getting the correct lengths in the triangle

In [295]:
plot_3d_with_geodesics(X_torus, gs, torch.vstack([c1_geodesic, d_geodesic]))

Another sanity check that this measure returns zero on the (flat) swiss roll.

In [304]:
k, gs, c1_geodesic, d_geodesic = alexandrov_curvature_of_triangle(swiss_roll.X.numpy(), swiss_roll_triangles[23], swiss_roll.geodesics, return_extras = True)

In [305]:
k

tensor(-0.0006, dtype=torch.float64)

Indeed, all of the well-behaved triangles have near-zero curvature. The method is working.

In [307]:
#|export
def compute_triangle_curvatures(X:np.ndarray, # pointcloud
                                D:np.ndarray, # distances on pointcloud; preferable manifold distances (PHATE). Used for creating triangles. Doesn't need to come from the geodesics.
                                geodesic_fn, # function that takes start_points, end_points and ts and returns (a list of geodesics, length of each geodesic)
                                num_triangles = 100, 
                                min_edge_length = 1,  # Must tune to each dataset. Defaults for torus.
                                max_edge_length = 1.5,
                                ):
    """Compures the Alexandrov curvature of sampled triangles. Returns ks, middle_idxs; ks is a list of Alexandrov curvatures, and middle_idxs is a list of the indices of the middle point of each triangle."""
    triangles = create_triangles_from_pointcloud(X, D, min_edge_length, max_edge_length, num_triangles)
    ks = []
    middle_idxs = []
    for t in tqdm(triangles):
        k, gs, c1_geodesic, d_geodesic = alexandrov_curvature_of_triangle(X, t, geodesic_fn, return_extras = True)
        ks.append(k)
        middle_idxs.append(d_geodesic[len(d_geodesic)//2])
    return ks, middle_idxs

# Tests

In [259]:
from autometric.datasets import Torus, Sphere

With Torus

In [308]:
torus = Torus(num_points = 3000)
X_torus = torus.X.numpy()
D_euc = pairwise_distances(X_torus, X_torus) # preferably use PHATE distances here

In [309]:
ks, idxs = compute_triangle_curvatures(X_torus, D_euc, 
                                       torus.geodesics, # a geodesic function
                                       num_triangles = 100, min_edge_length = 1, max_edge_length = 1.5) # pretuned edge lengths

  0%|          | 0/100 [00:00<?, ?it/s]

KeyboardInterrupt: 

With Sphere, showing how to tune the triangle sizes.

In [296]:
sphere = Sphere(num_points = 10000)
X_sphere = sphere.X
D_euc_sphere = pairwise_distances(X_sphere, X_sphere)

In [313]:
triangles = create_triangles_from_pointcloud(X_sphere, D_euc_sphere, min_dist = 0.7, max_dist=1, num_triangles=14)
plot_triangle_in_3d(X_sphere, triangles[0], sphere.geodesics)

/tmp/ipykernel_210617/792130572.py:5: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

/tmp/ipykernel_210617/792130572.py:6: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [311]:
ks, idxs = compute_triangle_curvatures(X_sphere, D_euc_sphere, sphere.geodesics, num_triangles = 100, min_edge_length = 0.7, max_edge_length = 1) # pretuned edge lengths

  0%|          | 0/100 [00:00<?, ?it/s]

/tmp/ipykernel_210617/792130572.py:5: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

/tmp/ipykernel_210617/792130572.py:6: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [312]:
ks

[tensor(0.0279, dtype=torch.float64),
 tensor(0.0271, dtype=torch.float64),
 tensor(0.0277, dtype=torch.float64),
 tensor(0.0240, dtype=torch.float64),
 tensor(0.0244, dtype=torch.float64),
 tensor(0.0512, dtype=torch.float64),
 tensor(0.0016, dtype=torch.float64),
 tensor(0.0110, dtype=torch.float64),
 tensor(0.0087, dtype=torch.float64),
 tensor(0.0184, dtype=torch.float64),
 tensor(0.0173, dtype=torch.float64),
 tensor(0.0348, dtype=torch.float64),
 tensor(0.0360, dtype=torch.float64),
 tensor(0.0068, dtype=torch.float64),
 tensor(0.0268, dtype=torch.float64),
 tensor(0.0196, dtype=torch.float64),
 tensor(0.0054, dtype=torch.float64),
 tensor(0.0296, dtype=torch.float64),
 tensor(0.0211, dtype=torch.float64),
 tensor(0.0334, dtype=torch.float64),
 tensor(0.0030, dtype=torch.float64),
 tensor(0.0301, dtype=torch.float64),
 tensor(0.0152, dtype=torch.float64),
 tensor(0.0087, dtype=torch.float64),
 tensor(0.0196, dtype=torch.float64),
 tensor(0.0247, dtype=torch.float64),
 tensor(0.02

In [277]:
k, gs, c1_geodesic, d_geodesic = alexandrov_curvature_of_triangle(X_sphere, triangles[0], sphere.geodesics, return_extras = True)

/tmp/ipykernel_210617/792130572.py:5: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).

/tmp/ipykernel_210617/792130572.py:6: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [278]:
plot_3d_with_geodesics(X_sphere, gs, torch.vstack([c1_geodesic, d_geodesic]))

In [317]:
# sync changes to the library
from IPython.display import display, Javascript
import time
display(Javascript('IPython.notebook.save_checkpoint();'))
time.sleep(2)
!pixi run nbsync

<IPython.core.display.Javascript object>

✨ Pixi task (default): nbdev_export
⠁ activating environment                                                                 